In [1]:
import torch
from utils.Datasets import prepareListwiseDataset

from utils.CollateFunc import NBestSampler, BatchSampler, crossNBestBatch
from torch.utils.data import DataLoader
import json

# PBERT Visualization

In [2]:
from utils.PrepareModel import prepareNBestCrossBert, preparePBert
from bertviz import model_view, head_view
import os

In [3]:
PBERT_checkpoint_path = "/mnt/disk6/Alfred/Rescoring/src/RescoreBert/checkpoint/aishell/NBestCrossBert/noLM/PBERT/50best/RescoreBert_PBERT_batch256_lr1e-7_Freeze-1/checkpoint_train_best_CER.pt"

In [4]:
os.environ['CUDA_VISIBLE_DEVICES']='3'
device = torch.device("cpu")
PBert_model, tokenizer = preparePBert(
    'aishell',
    device,
    False,
    'KL'
)
PBert_model = PBert_model.to(device)

Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


output_attention:KL


In [38]:
PBert_model.load_state_dict(torch.load(PBERT_checkpoint_path)['model'])
# checkpoint.keys()
# model.eval()

<All keys matched successfully>

# NBest Bert Visualization

In [9]:
NBestBert = "/mnt/disk6/Alfred/Rescoring/src/RescoreBert/checkpoint/aishell/NBestCrossBert/noLM/Normal_lstm_KL_sortByLength_dropout0.3_seed42/50best/batch256_lr1e-7_freeze-1/checkpoint_train_best_CER.pt"

In [48]:
checkpoint = torch.load(NBestBert)
checkpoint['model'].keys()

dict_keys(['bert', 'concatLinear', 'clsConcatLinear', 'finalLinear', 'fuseAttend', 'lstm'])

In [51]:
os.environ['CUDA_VISIBLE_DEVICES']='1'
device = torch.device("cpu")
NBest_model, tokenizer = prepareNBestCrossBert(
    'aishell',
    device,
    lstm_dim = 1024,
    useNbestCross = False,
    lossType = 'KL',
    concatCLS = False
)
NBest_model.load_state_dict(checkpoint['model'])
NBest_model = NBest_model.to(device)

Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).



not concatCLS


In [44]:
hyp_1 = "但 因 为 聚 集 了 过 多 公 共 思 源"
hyp_2 = "但 因 为 聚 集 了 过 多 公 共 四 元"
hyp_3 = "但 因 为 聚 集 了 过 多 公 共 思 员"
ref = "但 因 为 聚 集 了 过 多 公 共 资 源"

In [41]:
hyp_1 = "二 人 一 直 先 少 回 应"
hyp_2 = "二 零 一 直 先 少 回 应"
hyp_3 = "二 零 一 直 鲜 少 回 应"
ref = "二 人 一 直 鲜 少 回 应"

In [124]:
hyp_1 = "北 京 申 办 冬 奥 影 响 远 超 申 办 本 身" # PBert
ref = "北 京 申 办 冬 奥 影 响 远 超 承 办 本 身" # NBestBert

In [115]:
hyp_1 = "在 世 锦 赛 决 赛 减 路 前 突 感 不 适" # NBestBert
ref = "在 世 锦 赛 决 赛 检 录 前 突 感 不 适" # PBert

In [49]:
hyps = [hyp_2,  ref]
index = 0
print(hyps)

['但 因 为 聚 集 了 过 多 公 共 四 元', '但 因 为 聚 集 了 过 多 公 共 资 源']


# NBestBert

In [50]:
hyp_ids = tokenizer.encode(hyps[index], return_tensors='pt')

output = PBert_model.bert(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 14, 14])
[CLS] 但 因 为 聚 集 了 过 多 公 共 四 元 [SEP]


<IPython.core.display.Javascript object>

In [126]:
hyp_ids = tokenizer.encode(hyps[index], return_tensors='pt')

output = NBest_model.bert(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 16, 16])
[CLS] 北 京 申 办 冬 奥 影 响 远 超 承 办 本 身 [SEP]


<IPython.core.display.Javascript object>

In [122]:
hyp_ids = tokenizer.encode(hyps[index], return_tensors='pt')

output = model.bert(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 15, 15])
[CLS] 在 世 锦 赛 决 赛 减 路 前 突 感 不 适 [SEP]


<IPython.core.display.Javascript object>

In [58]:
from transformers import BertModel
raw_model = BertModel.from_pretrained('bert-base-chinese')

Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [123]:
hyp_ids = tokenizer.encode(hyps[index], return_tensors='pt')

output = raw_model(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 15, 15])
[CLS] 在 世 锦 赛 决 赛 减 路 前 突 感 不 适 [SEP]


<IPython.core.display.Javascript object>

# MaskEMbedBert

In [8]:
MaskBertcheckpoint = "/mnt/disk6/Alfred/Rescoring/src/RescoreBert/checkpoint/aishell/NBestCrossBert/noLM/Normal_query_KL_sortByLength_concatMask_dropout0.3_seed42/50best/batch256_lr1e-7_freeze-1/checkpoint_train_best_CER.pt"
MaskAfterBertcheckpoint = "/mnt/disk6/Alfred/Rescoring/src/RescoreBert/checkpoint/aishell/NBestCrossBert/noLM/Normal_query_KL_sortByLength_concatMaskAfter_dropout0.3_seed42/50best/batch256_lr1e-7_freeze-1/checkpoint_train_best_CER.pt"
ConcatMaskCheckpoint = "/mnt/disk6/Alfred/Rescoring/src/RescoreBert/checkpoint/aishell/NBestCrossBert/noLM/Normal_query_KL_sortByLength_concatCLS_concatMaskAfter_dropout0.3_seed42/50best/batch256_lr1e-7_freeze-1/checkpoint_train_best_CER.pt"

In [9]:
MaskBert, tokenizer = prepareNBestCrossBert(
    dataset = 'aishell',
    device = device, 
    fuseType = 'query',
    concatCLS = False
)

MaskAfterBert, tokenizer = prepareNBestCrossBert(
    dataset = 'aishell',
    device = device, 
    fuseType = 'query',
    concatCLS = False
)

MaskConcatBert, tokenizer = prepareNBestCrossBert(
    dataset = 'aishell',
    device = device, 
    fuseType = 'query',
    concatCLS = True
)

NO concatCLS


Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


NO concatCLS


Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Using concatCLS


Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [13]:
MaskBert.load_state_dict(torch.load(MaskBertcheckpoint)['model'])
MaskAfterBert.load_state_dict(torch.load(MaskAfterBertcheckpoint)['model'])
MaskConcatBert.load_state_dict(torch.load(ConcatMaskCheckpoint)['model'])

In [16]:
hyp_1 = "但 因 为 聚 集 了 过 多 公 共 思 源"
hyp_2 = "但 因 为 聚 集 了 过 多 公 共 四 元"
hyp_3 = "但 因 为 聚 集 了 过 多 公 共 思 员"
ref = "但 因 为 聚 集 了 过 多 公 共 资 源"

In [18]:
hyp_1_mask = hyp_1 + "[MASK]"
hyp_2_mask = hyp_2 + "[MASK]"
hyp_3_mask = hyp_3 + "[MASK]"
ref_mask = ref + "[MASK]"

In [30]:
hyps = [hyp_1, hyp_2, hyp_3, ref]
index = 3

In [33]:
hyp_ids = tokenizer.encode(hyps[index], return_tensors='pt')
mask = tokenizer.convert_tokens_to_ids(["[MASK]"])
mask = torch.tensor(mask).unsqueeze(0)
hyp_ids = torch.cat([hyp_ids, mask], dim = -1)

output = MaskAfterBert.bert(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 15, 15])
[CLS] 但 因 为 聚 集 了 过 多 公 共 四 元 [SEP] [MASK]


<IPython.core.display.Javascript object>

In [32]:
hyps_mask = [hyp_1_mask, hyp_2_mask, hyp_3_mask, ref_mask]
index = 0

In [34]:
hyp_ids = tokenizer.encode(hyps_mask[index], return_tensors='pt')

output = MaskAfterBert.bert(
    input_ids = hyp_ids,
    output_attentions = True
)
attention = output.attentions

tokens = tokenizer.convert_ids_to_tokens(hyp_ids[0].tolist())
single_attention = [att for att in attention]
print(single_attention[-1].shape)
print(" ".join(tokens))
head_view(attention = single_attention, tokens = tokens) #, html_action='return')

torch.Size([1, 12, 15, 15])
[CLS] 但 因 为 聚 集 了 过 多 公 共 四 元 [MASK] [SEP]


<IPython.core.display.Javascript object>

In [91]:
PBertJson = "/mnt/disk6/Alfred/Rescoring/data/result/aishell/noLM/test/NBestCrossBert_PBERT_result.json"
NBestCrossJson = "/mnt/disk6/Alfred/Rescoring/data/result/aishell/noLM/test/NBestCrossBert_lstm_KL_freeze-1_BestCER_result.json"
import json

In [97]:
with open(PBertJson) as P, open(NBestCrossJson) as N:
    P_result = json.load(P)
    N_result = json.load(N)
    
    
    for p, n in zip(P_result, N_result):
        if (p['check_1'] == 'Error' and n['check_1'] == 'Correct'):
            print(f"sit 1 :\npBert:{p['rescore_hyps']}\nNBestBert:{n['rescore_hyps']}")
        elif (p['check_1'] == 'Correct' and n['check_1'] == 'Error'):
            print(f"sit 2 :\npBert:{p['rescore_hyps']}\nNBestBert:{n['rescore_hyps']}")

sit 1 :
pBert:市 场 技 术 已 不 可 同 日 而 语
NBestBert:市 场 基 数 已 不 可 同 日 而 语
sit 1 :
pBert:美 国 东 卡 罗 莱 纳 大 学 和 维 托 森 林 大 学 的 研 究 者 认 为
NBestBert:美 国 东 卡 罗 莱 纳 大 学 和 维 克 森 林 大 学 的 研 究 者 认 为
sit 2 :
pBert:并 让 年 轻 跑 者 作 为 参 照
NBestBert:便 让 年 轻 跑 者 作 为 参 照
sit 2 :
pBert:来 自 全 球 四 七 个 国 家 和 地 区 的 二 零 零 零 多 名 选 手 参 赛
NBestBert:来 自 全 球 四 七 个 国 家 和 地 区 的 二 零 零 多 名 选 手 参 赛
sit 1 :
pBert:可 以 更 好 地 体 现 代 价 公 平
NBestBert:可 以 更 好 地 体 现 代 际 公 平
sit 2 :
pBert:并 未 能 给 这 些 公 司 带 来 其 他 的 效 应
NBestBert:并 未 能 给 这 些 公 司 带 来 其 他 的 效 益
sit 1 :
pBert:在 投 资 和 发 展 海 外 市 场 上
NBestBert:在 融 资 和 发 展 海 外 市 场 上
sit 1 :
pBert:北 京 申 办 冬 奥 影 响 远 超 申 办 本 身
NBestBert:北 京 申 办 冬 奥 影 响 远 超 承 办 本 身
sit 1 :
pBert:平 潭 曾 经 三 次 申 办 冬 奥 会
NBestBert:平 昌 曾 经 三 次 申 办 冬 奥 会
sit 2 :
pBert:一 四 年 前 轰 动 东 莞 沙 田 的 一 起 命 案
NBestBert:一 四 年 前 轰 动 东 莞 沙 田 的 一 起 密 案
sit 1 :
pBert:但 地 产 商 的 效 果 预 期 不 断 提 高
NBestBert:当 地 产 商 的 效 果 预 期 不 断 提 高
sit 1 :
pBert:许 多 数 码 新 产 品
NBestBert:许 多 数 字 新 产 品
sit 1 :
pBert:投 资 者 对 承 投 债 券 风 险 表 现 出 的 恐 慌
NBestBert:投 资 者 